# 初始化 CUDA 环境

In [1]:
import os
import subprocess

# Set environment for current kernel/session
cuda_home = "/usr/local/cuda-12.4"
os.environ["CUDA_HOME"] = cuda_home
os.environ["PATH"] = f"{cuda_home}/bin:" + os.environ.get("PATH", "")
os.environ["LD_LIBRARY_PATH"] = f"{cuda_home}/lib64:" + os.environ.get("LD_LIBRARY_PATH", "")

# Try to set /usr/local/cuda symlink to 12.4 (optional)
# subprocess.run(["sudo", "ln", "-sfn", cuda_home, "/usr/local/cuda"], check=False)

# Quick check
subprocess.run(["nvcc", "--version"], check=False)
# subprocess.run(["nvidia-smi"], check=False)

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2024 NVIDIA Corporation
Built on Tue_Feb_27_16:19:38_PST_2024
Cuda compilation tools, release 12.4, V12.4.99
Build cuda_12.4.r12.4/compiler.33961263_0


CompletedProcess(args=['nvcc', '--version'], returncode=0)

# 安装 Python 包

In [ ]:
# 手动运行⬇️
# !sudo apt install colmap aria2 -y

!pip install torch==2.4.0+cu124 torchvision==0.19.0+cu124 torchaudio==2.4.0+cu124 torchtext==0.18.0 torchdata==0.7.1 --extra-index-url https://download.pytorch.org/whl/cu124
!pip install opencv-python scipy torchgeometry chumpy scikit-image kornia json-tricks colorama
# ------- install pytorch3d-0.7.8 from git
!pip install --no-build-isolation git+https://github.com/facebookresearch/pytorch3d.git@V0.7.8
# ------- install mmcv-2.1.0 from git
!pip install --no-build-isolation git+https://github.com/open-mmlab/mmcv.git@v2.1.0
!pip install mmpose mmdet numpy==1.23.5 face-alignment==1.3.4 plyfile pyrender smplx lpips yacs
# ------ install diff-gaussian-rasterization-depth
!pip install --no-build-isolation git+https://github.com/leo-frank/diff-gaussian-rasterization-depth

# 克隆仓库 + 下载资源文件

In [4]:
%env SUBJECT_ID = gyeongsik
%env PROJ_PATH = /home/wh/repos/ExAvatar
%cd /home/wh/repos/ExAvatar

env: SUBJECT_ID=gyeongsik
env: PROJ_PATH=/home/wh/repos/ExAvatar
/home/wh/repos/ExAvatar


## 克隆仓库

In [ ]:
%cd ./fitting/tools

!git clone https://github.com/yfeng95/DECA
!git clone https://github.com/mks0601/Hand4Whole_RELEASE
!git clone https://github.com/open-mmlab/mmpose
!git clone https://github.com/facebookresearch/segment-anything
!git clone https://github.com/DepthAnything/Depth-Anything-V2

%cd ../..

## 下载资源文件

In [ ]:
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_FEMALE.npz -d ./fitting/common/utils/human_model_files/smplx -o SMPLX_FEMALE.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_MALE.npz -d ./fitting/common/utils/human_model_files/smplx -o SMPLX_MALE.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_NEUTRAL.npz -d ./fitting/common/utils/human_model_files/smplx -o SMPLX_NEUTRAL.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/MANO_SMPLX_vertex_ids.pkl -d ./fitting/common/utils/human_model_files/smplx -o MANO_SMPLX_vertex_ids.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPL-X__FLAME_vertex_ids.npy -d ./fitting/common/utils/human_model_files/smplx -o SMPL-X__FLAME_vertex_ids.npy
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/smplx_flip_correspondences.npz -d ./fitting/common/utils/human_model_files/smplx -o smplx_flip_correspondences.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/raw/main/data/smplx_uv.obj -d ./fitting/common/utils/human_model_files/smplx/smplx_uv -o smplx_uv.obj
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame_dynamic_embedding.npy -d ./fitting/common/utils/human_model_files/flame -o flame_dynamic_embedding.npy
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/FLAME_FEMALE.pkl -d ./fitting/common/utils/human_model_files/flame -o FLAME_FEMALE.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/FLAME_MALE.pkl -d ./fitting/common/utils/human_model_files/flame -o FLAME_MALE.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/FLAME_NEUTRAL.pkl -d ./fitting/common/utils/human_model_files/flame -o FLAME_NEUTRAL.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/flame_static_embedding.pkl -d ./fitting/common/utils/human_model_files/flame -o flame_static_embedding.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/FLAME_texture.npz -d ./fitting/common/utils/human_model_files/flame -o FLAME_texture.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/2019/generic_model.pkl -d ./fitting/common/utils/human_model_files/flame/2019 -o generic_model.pkl

!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPL_NEUTRAL.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smpl -o SMPL_NEUTRAL.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_to_J14.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPLX_to_J14.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/mano/MANO_LEFT.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/mano -o MANO_LEFT.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/mano/MANO_RIGHT.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/mano -o MANO_RIGHT.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/FLAME_NEUTRAL.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/flame -o FLAME_NEUTRAL.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame_dynamic_embedding.npy -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/flame -o flame_dynamic_embedding.npy
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/show/resolve/main/data/flame/flame_static_embedding.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/flame -o flame_static_embedding.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/MANO_SMPLX_vertex_ids.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o MANO_SMPLX_vertex_ids.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPL-X__FLAME_vertex_ids.npy -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPL-X__FLAME_vertex_ids.npy
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_NEUTRAL.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPLX_NEUTRAL.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_NEUTRAL.npz -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPLX_NEUTRAL.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_MALE.npz -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPLX_MALE.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPLX_FEMALE.npz -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smplx -o SMPLX_FEMALE.npz
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPL_MALE.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smpl -o SMPL_MALE.pkl
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/camenduru/SMPLer-X/resolve/main/SMPL_FEMALE.pkl -d ./fitting/tools/Hand4Whole_RELEASE/common/utils/human_model_files/smpl -o SMPL_FEMALE.pkl

!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://download.openmmlab.com/mmpose/v1/projects/rtmpose/rtmdet_m_8xb32-100e_coco-obj365-person-235e8209.pth -d ./fitting/tools/mmpose -o rtmdet_m_8xb32-100e_coco-obj365-person-235e8209.pth
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/yzd-v/DWPose/resolve/main/dw-ll_ucoco_384.pth -d ./fitting/tools/mmpose -o dw-ll_ucoco_384.pth

!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/HCMUE-Research/SAM-vit-h/resolve/main/sam_vit_h_4b8939.pth -d ./fitting/tools/segment-anything -o sam_vit_h_4b8939.pth

!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://hf-mirror.com/depth-anything/Depth-Anything-V2-Large/resolve/main/depth_anything_v2_vitl.pth -d ./fitting/tools/Depth-Anything-V2/checkpoints -o depth_anything_v2_vitl.pth


In [8]:
!cp ./fitting/common/utils/human_model_files/flame/2019/generic_model.pkl ./fitting/tools/DECA/data/generic_model.pkl
!cp -r ./fitting/common/utils/human_model_files ./avatar/common/utils/human_model_files

# !sed -i.bak 's/1 - mask_d0_d1/~mask_d0_d1/' /home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/torchgeometry/core/conversions.py
# !sed -i.bak 's/\(1 - \)\(mask_[^ ]*\)/~\2/g' /home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/torchgeometry/core/conversions.py

## 下面的文件需要手动下载，并放到指定目录

In [ ]:
# 手动下载

# 'https://drive.google.com/uc?id=1rp8kdyLPvErw2dTmqtjISRVvQLj6Yzje' -O ./fitting/tools/DECA/data/deca_model.tar
# 'https://drive.google.com/file/d/1r0LfI_ATI8NmhOj4y8eqLlEDdNQj5SCV' -O ./fitting/tools/Hand4Whole_RELEASE/demo/snapshot_6.pth.tar

# 手动下载 FLAME2020 模型并解压到指定目录 ./fitting/tools/DECA/data/FLAME2020

%cd ./fitting/tools

!python copy_code.py

%cd ../..

/home/wh/repos/ExAvatar/fitting/tools
/home/wh/repos/ExAvatar


# 数据预处理

In [ ]:
%cd $PROJ_PATH
%cd ./fitting/tools

# Extract frames from video.mp4 to <root_path>/frames/
!python extract_frames.py --root_path $PROJ_PATH/fitting/data/Custom/data/$SUBJECT_ID

%cd ../..

In [ ]:
%cd ./fitting/tools

# 生成 frame_list 文件
# --all 起始帧 结束帧； --train 起始帧 间隔帧数； --test 起始帧 间隔帧数
!python generate_frame_list.py --all 110 645 --train 114 6 --test 115 6

!mv ./frame_list_all.txt ../data/Custom/data/$SUBJECT_ID
!mv ./frame_list_train.txt ../data/Custom/data/$SUBJECT_ID
!mv ./frame_list_test.txt ../data/Custom/data/$SUBJECT_ID
%cd ../..

/home/wh/repos/ExAvatar/fitting/tools
Generated ./frame_list_all.txt with 536 frames.
Generated ./frame_list_train.txt with 89 frames.
Generated ./frame_list_test.txt with 89 frames.
/home/wh/repos/ExAvatar


In [ ]:
# 替换配置文件中的 dataset 字段
!sed -i "s/^\([[:space:]]*\)dataset *= *.*/\1dataset = 'Custom' # 'NeuMan', 'Custom', 'XHumans'/" ./fitting/main/config.py

## run.py

`run.py` 会在 `./fitting/data/Custom/data/$SUBJECT_ID` 目录下输出以下内容：  
- 相机参数 (`cam_params`)
- 初始的 **FLAME** 参数 (`flame_init/flame_params`)  
- 初始的 **SMPL-X** 参数 (`smplx_init`)  
- **二维全身关键点** (`keypoints_whole_body`)  
- **优化/平滑后的 SMPL-X 参数** (`smplx_optimized`)  
- **展开（unwrapped）的面部纹理** (``)

In [ ]:
%cd ./fitting/tools

# Option 1: Use COLMAP to reconstruct camera parameters
# !python run.py --root_path $PROJ_PATH/fitting/data/Custom/data/$SUBJECT_ID --use_colmap

# Option 2: Use virtual camera parameters
!python run.py --root_path $PROJ_PATH/fitting/data/Custom/data/$SUBJECT_ID

%cd ../..

In [ ]:
import os
import os.path as osp
from glob import glob
import sys

use_colmap = False
root_path = "/home/wh/repos/ExAvatar/fitting/data/Custom/data/gyeongsik"
os.chdir(root_path + "/../../../../tools")

if root_path[-1] == '/':
    subject_id = root_path.split('/')[-2]
else:
    subject_id = root_path.split('/')[-1]

# remove unnecessary frames
with open(osp.join(root_path, 'frame_list_all.txt')) as f:
    frame_idx_list = [int(x) for x in f.readlines()]
img_path_list = glob(osp.join(root_path, 'frames', '*.png'))
for img_path in img_path_list:
    frame_idx = int(img_path.split('/')[-1][:-4])
    if frame_idx not in frame_idx_list:
        cmd = 'rm ' + img_path
        result = os.system(cmd)
        if (result != 0):
            print('something bad happened when removing unnecessary frames. terminate the script.')
            sys.exit()

# make camera parameters
if use_colmap:
    os.chdir('./COLMAP')
    cmd = 'python run_colmap.py --root_path ' + root_path
    print(cmd)
    result = os.system(cmd)
    if (result != 0):
        print('something bad happened when running COLMAP to get camera parameters. terminate the script.')
        sys.exit()
else:
    cmd = 'python make_virtual_cam_params.py --root_path ' + root_path
    print(cmd)
    result = os.system(cmd)
    if (result != 0):
        print('something bad happened when making the virtual camera parameters. terminate the script.')
        sys.exit()

# DECA (get initial FLAME parameters)
os.chdir('./DECA')
cmd = 'python run_deca.py --root_path ' + root_path
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when running DECA. terminate the script.')
    sys.exit()
os.chdir('..')

# Hand4Whole (get initial SMPLX parameters)
os.chdir('./Hand4Whole_RELEASE/demo')
cmd = 'python run_hand4whole.py --gpu 0 --root_path ' + root_path
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when running Hand4Whole. terminate the script.')
    sys.exit()
os.chdir('../../')

# mmpose (get 2D whole-body keypoints)
os.chdir('./mmpose')
cmd = 'python run_mmpose.py --root_path ' + root_path
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when running mmpose. terminate the script.')
    sys.exit()
os.chdir('..')

# fit SMPLX
os.chdir('../main')
cmd = 'python fit.py --subject_id ' + subject_id
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when fitting. terminate the script.')
    sys.exit()
os.chdir('../tools')
cmd = 'mv ' + osp.join('..', 'output', 'result', subject_id, '*') + ' ' + osp.join(root_path, '.')
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when moving the fitted files to root_path. terminate the script.')
    sys.exit()

# unwrap textures of FLAME
os.chdir('../main')
cmd = 'python unwrap.py --subject_id ' + subject_id
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when unwrapping the face images to FLAME UV texture. terminate the script.')
    sys.exit()
os.chdir('../tools')
cmd = 'mv ' + osp.join('..', 'output', 'result', subject_id, 'unwrapped_textures', '*') + ' ' + osp.join(root_path, 'smplx_optimized', '.')
result = os.system(cmd)
if (result != 0):
    print('something bad happened when moving the unwrapped FLAME UV texture to root_path. terminate the script.')
    sys.exit()

# smooth SMPLX
cmd = 'python smooth_smplx_params.py --root_path ' + root_path
print(cmd)
result = os.system(cmd)
if (result != 0):
    print('something bad happened when smoothing smplx parameters. terminate the script.')
    sys.exit()



# Avatar

In [ ]:
!cp -r ./fitting/common/utils/human_model_files ./avatar/common/utils
!mkdir -p ./avatar/data/Custom/data/$SUBJECT_ID
!cp ./fitting/data/Custom/data/$SUBJECT_ID/video.mp4 ./avatar/data/Custom/data/$SUBJECT_ID

In [38]:
%cd ./fitting/tools

%cd segment-anything
!python run_sam.py --root_path $PROJ_PATH/fitting/data/Custom/data/$SUBJECT_ID
%cd ..

%cd ../..

/home/wh/repos/ExAvatar/fitting/tools
/home/wh/repos/ExAvatar/fitting/tools/segment-anything
/home/wh/repos/ExAvatar/fitting/tools/segment-anything/segment_anything/build_sam.py:105: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub

In [ ]:
%cd ./fitting/tools

%cd Depth-Anything-V2
# Background option 1: static video
!python run_depth_anything.py --root_path $PROJ_PATH/fitting/data/Custom/data/$SUBJECT_ID
# Background option 2: dynamic video
# Just proceed to next step
%cd ..

%cd ../..

# Train

In [46]:
!sed -i "s/^\([[:space:]]*\)dataset *= *.*/\1dataset = 'Custom' # 'NeuMan', 'Custom', 'XHumans'/" ./avatar/main/config.py
!cp -r ./fitting/data/Custom/data/gyeongsik ./avatar/data/Custom/data

In [55]:
%cd ./avatar/main

!python train.py --subject_id $SUBJECT_ID

%cd ../..

/home/wh/repos/ExAvatar/avatar/main


24724.71s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


/home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/smplx/body_models.py:1967: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)
  dynamic_lmk_b_coords = torch.tensor(
12-30 23:19:27 Creating dataset...
Load virtual camera parameters
Load background point cloud from monocular depth estimator
Setting up [LPIPS] perceptual loss: trunk [vgg], v[0.1], spatial [off]
/home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weigh

In [58]:
%cd ./avatar/main

!python test.py --subject_id $SUBJECT_ID --test_epoch 4

%cd ../..

/home/wh/repos/ExAvatar/avatar/main


57572.87s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


/home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/smplx/body_models.py:1967: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)
  dynamic_lmk_b_coords = torch.tensor(
12-31 08:26:55 Creating dataset...
Load virtual camera parameters
Load background point cloud from monocular depth estimator
12-31 08:27:42 Load checkpoint from /home/wh/repos/ExAvatar/avatar/main/../output/model_dump/gyeongsik/snapshot_4.pth
/home/wh/repos/ExAvatar/avatar/main/../common/base.py:179: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.m

# Visualization

In [60]:
%cd ./avatar/main

!python get_neutral_pose.py --subject_id $SUBJECT_ID --test_epoch 4

%cd ../..

/home/wh/repos/ExAvatar/avatar/main


97507.44s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


/home/wh/repos/miniforge3/envs/exavt/lib/python3.10/site-packages/smplx/body_models.py:1967: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)
  dynamic_lmk_b_coords = torch.tensor(
12-31 19:32:29 Load checkpoint from /home/wh/repos/ExAvatar/avatar/main/../output/model_dump/gyeongsik/snapshot_4.pth
/home/wh/repos/ExAvatar/avatar/main/../common/base.py:179: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. Th

# Animation

In [ ]:
%cd ./avatar/main

# 固定视角的 Animated Avatar Video
!python animate.py --subject_id $SUBJECT_ID --test_epoch 4 --motion_path $PROJ_PATH/avatar/data/Custom/data/$SUBJECT_ID

%cd ../..

In [ ]:
%cd ./avatar/main

# 旋转视角的 Animated Avatar Video，输出到 ./avatar/main/$SUBJECT_ID.mp4
!python animate_view_rot.py --subject_id $SUBJECT_ID --test_epoch 4 --motion_path  $PROJ_PATH/avatar/data/Custom/data/$SUBJECT_ID

%cd ../..